# Bulutta Veri Bilimi: "Azure ML SDK" Yöntemi

## Giriş

Bu not defterinde, Azure ML SDK kullanarak bir modeli eğitme, dağıtma ve tüketme işlemlerini Azure ML üzerinden nasıl gerçekleştireceğimizi öğreneceğiz.

Ön Koşullar:
1. Bir Azure ML çalışma alanı oluşturdunuz.
2. [Heart Failure dataset](https://www.kaggle.com/andrewmvd/heart-failure-clinical-data) verisetini Azure ML'e yüklediniz.
3. Bu not defterini Azure ML Studio'ya yüklediniz.

Sonraki adımlar şunlardır:

1. Mevcut bir Çalışma Alanında bir Deney oluşturun.
2. Bir Hesaplama kümesi oluşturun.
3. Verisetini yükleyin.
4. AutoML'i AutoMLConfig kullanarak yapılandırın.
5. AutoML deneyini çalıştırın.
6. Sonuçları inceleyin ve en iyi modeli alın.
7. En iyi modeli kaydedin.
8. En iyi modeli dağıtın.
9. Uç noktayı kullanın.

## Azure Machine Learning SDK'ya Özgü İçe Aktarımlar


In [ ]:
from azureml.core import Workspace, Experiment
from azureml.core.compute import AmlCompute
from azureml.train.automl import AutoMLConfig
from azureml.widgets import RunDetails
from azureml.core.model import InferenceConfig, Model
from azureml.core.webservice import AciWebservice

## Çalışma Alanını Başlat  
Kalıcı yapılandırmadan bir çalışma alanı nesnesi başlatın. Yapılandırma dosyasının .\config.json konumunda bulunduğundan emin olun.  


In [ ]:
ws = Workspace.from_config()
print(ws.name, ws.resource_group, ws.location, ws.subscription_id, sep = '\n')

## Azure ML deneyi oluşturma

Az önce başlattığımız çalışma alanında 'aml-experiment' adında bir deney oluşturalım.


In [ ]:
experiment_name = 'aml-experiment'
experiment = Experiment(ws, experiment_name)
experiment

## Bir Hesaplama Kümesi Oluşturun
AutoML çalıştırmanız için bir [hesaplama hedefi](https://docs.microsoft.com/azure/machine-learning/concept-azure-machine-learning-architecture#compute-target) oluşturmanız gerekecek.


In [ ]:
aml_name = "heart-f-cluster"
try:
    aml_compute = AmlCompute(ws, aml_name)
    print('Found existing AML compute context.')
except:
    print('Creating new AML compute context.')
    aml_config = AmlCompute.provisioning_configuration(vm_size = "Standard_D2_v2", min_nodes=1, max_nodes=3)
    aml_compute = AmlCompute.create(ws, name = aml_name, provisioning_configuration = aml_config)
    aml_compute.wait_for_completion(show_output = True)

cts = ws.compute_targets
compute_target = cts[aml_name]

## Veriler
Veri kümesini Azure ML'ye yüklediğinizden ve anahtarın veri kümesiyle aynı adı taşıdığından emin olun.


In [ ]:
key = 'heart-failure-records'
dataset = ws.datasets[key]
df = dataset.to_pandas_dataframe()
df.describe()

## Otomatik ML Yapılandırması


In [ ]:
automl_settings = {
    "experiment_timeout_minutes": 20,
    "max_concurrent_iterations": 3,
    "primary_metric" : 'AUC_weighted'
}

automl_config = AutoMLConfig(compute_target=compute_target,
                             task = "classification",
                             training_data=dataset,
                             label_column_name="DEATH_EVENT",
                             enable_early_stopping= True,
                             featurization= 'auto',
                             debug_log = "automl_errors.log",
                             **automl_settings
                            )

## Otomatik ML Çalıştırma


In [ ]:
remote_run = experiment.submit(automl_config)

In [ ]:
RunDetails(remote_run).show()

In [ ]:
best_run, fitted_model = remote_run.get_output()

In [ ]:
best_run.get_properties()

In [ ]:
model_name = best_run.properties['model_name']
script_file_name = 'inference/score.py'
best_run.download_file('outputs/scoring_file_v_1_0_0.py', 'inference/score.py')
description = "aml heart failure project sdk"
model = best_run.register_model(model_name = model_name,
                                description = description,
                                tags = None)

## En İyi Modeli Dağıt

En iyi modeli dağıtmak için aşağıdaki kodu çalıştırın. Dağıtımın durumunu Azure ML portalında görebilirsiniz. Bu adım birkaç dakika sürebilir.


In [ ]:
inference_config = InferenceConfig(entry_script=script_file_name, environment=best_run.get_environment())

aciconfig = AciWebservice.deploy_configuration(cpu_cores = 1,
                                               memory_gb = 1,
                                               tags = {'type': "automl-heart-failure-prediction"},
                                               description = 'Sample service for AutoML Heart Failure Prediction')

aci_service_name = 'automl-hf-sdk'
aci_service = Model.deploy(ws, aci_service_name, [model], inference_config, aciconfig)
aci_service.wait_for_deployment(True)
print(aci_service.state)

## Uç Noktayı Tüket

Aşağıdaki giriş örneğine girdiler ekleyebilirsiniz.


In [ ]:
data = {
    "data":
    [
        {
            'age': "60",
            'anaemia': "false",
            'creatinine_phosphokinase': "500",
            'diabetes': "false",
            'ejection_fraction': "38",
            'high_blood_pressure': "false",
            'platelets': "260000",
            'serum_creatinine': "1.40",
            'serum_sodium': "137",
            'sex': "false",
            'smoking': "false",
            'time': "130",
        },
    ],
}

test_sample = str.encode(json.dumps(data))

In [ ]:
response = aci_service.run(input_data=test_sample)
response


---

**Feragatname**:  
Bu belge, [Co-op Translator](https://github.com/Azure/co-op-translator) adlı yapay zeka çeviri hizmeti kullanılarak çevrilmiştir. Doğruluk için çaba göstersek de, otomatik çevirilerin hata veya yanlışlıklar içerebileceğini lütfen unutmayın. Orijinal belgenin kendi dilindeki hali, yetkili kaynak olarak kabul edilmelidir. Kritik bilgiler için profesyonel insan çevirisi önerilir. Bu çevirinin kullanımından kaynaklanan yanlış anlamalar veya yanlış yorumlamalardan sorumlu değiliz.
